In [1]:
%pip install joblib

Note: you may need to restart the kernel to use updated packages.


In [2]:
%pip install "dask[complete]"
%pip install dask_ml

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [3]:
from joblib import Parallel, delayed
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import Select   # seleccion de un dropdown
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
import time
import pandas as pd
import multiprocessing as mp
import warnings
warnings.filterwarnings('ignore')

from joblib._parallel_backends import LokyBackend
import asyncio

from tqdm.notebook import tqdm
import dask
import dask.dataframe as dd

In [4]:
#driver configuration
opciones=Options()

opciones.add_experimental_option('excludeSwitches', ['enable-automation'])
opciones.add_experimental_option('useAutomationExtension', False)
opciones.headless=False    # si True, no aperece la ventana (headless=no visible)
opciones.add_argument('--start-maximized')         # comienza maximizado
#opciones.add_argument('user-data-dir=selenium')    # mantiene las cookies
#opciones.add_extension('driver_folder/adblock.crx')       # adblocker
opciones.add_argument('--incognito')

In [5]:
meses = ["january","february","march","april","may","june","july","august","september","october","november","december"]
dias = []
for i in range(1,32):
    dias.append(str(i))


In [6]:
urls = []
for mes in meses:
    for dia in dias:
        urls.append(f'https://en.tutiempo.net/records/lemd/{dia}-{mes}-2022.html')

In [ ]:
# def extraer(url):
    
    
#     try:
#         # inicia el driver
#         driver=webdriver.Chrome(PATH)
#         driver.get(url)

#         time.sleep(2)

#         # acepta cookies
#         aceptar=driver.find_element(By.XPATH, '/html/body/div[18]/div[2]/div[1]/div[2]/div[2]/button[1]')
#         aceptar.click()

#         time.sleep(2)
#         aceptar=driver.find_element(By.XPATH, '//*[@id="DivAceptarCookies"]/div/a[2]')
#         aceptar.click()

#         day = driver.find_elements(By.XPATH,'//table//tbody//tr')[1].text
#         table = [row.text.split('\n')[0:3]+row.text.replace(' km/h','').split('\n')[-1].split(' ',2)
#          for row in driver.find_elements(By.XPATH,'//table//tbody//tr')[3:98:2]]
        
#         columns = ["Day","Hour","Condition","Temperature","Wind","Relative_hum","Pressure"]
        
#         for i in table:
#             i.insert(0,day)
#     except:
#         print(url)

        
#     return pd.DataFrame(table, columns=columns)

In [25]:
def extraer(url):
    table = []  # Inicializa table como una lista vacía
    columns = []
    
    try:
        # inicia el driver
        driver = webdriver.Chrome()
        driver.get(url)


        # acepta cookies
        aceptar = driver.find_element(By.XPATH,'/html/body/div[18]/div[2]/div[1]/div[2]/div[2]/button[1]')
        aceptar.click()

        #time.sleep(2)
        #aceptar = WebDriverWait(driver, 10).until(driver.find_element(By.XPATH, '//*[@id="DivAceptarCookies"]/div/a[2]'))
        aceptar = driver.find_element(By.XPATH, '//*[@id="DivAceptarCookies"]/div/a[2]')
        aceptar.click()

        day = driver.find_elements(By.XPATH, '//table//tbody//tr')[1].text
        table = [row.text.split('\n')[0:3] + row.text.replace(' km/h', '').split('\n')[-1].split(' ', 2)
                 for row in driver.find_elements(By.XPATH, '//table//tbody//tr')[3::2]]

        columns = ["Day", "Hour", "Condition", "Temperature", "Wind", "Relative_hum", "Pressure"]

        for i in table:
            i.insert(0, day)
            
        return pd.DataFrame(table, columns=columns)
        
    except Exception as e:  # Captura cualquier excepción y muestra el mensaje de error
        print(f"Error: {e}")
        print(f"Error en la URL: {url}")
        # En caso de error, simplemente se devolverá la lista vacía 'table'
        return pd.DataFrame(table, columns=columns) 
    driver.quit()
#     return pd.DataFrame(table, columns=columns)

In [30]:
paralelo = Parallel(n_jobs=8, verbose=True)


lst_df = paralelo(delayed(extraer)(url) for url in tqdm(urls[0:31]))

  0%|          | 0/31 [00:00<?, ?it/s]

[Parallel(n_jobs=8)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=8)]: Done  31 out of  31 | elapsed:  1.6min finished


Day                   Hour          Condition  \
0       Saturday 1 January 2022                  00:00              Clear   
1       Saturday 1 January 2022                  00:30              Clear   
2       Saturday 1 January 2022                  01:00              Clear   
3       Saturday 1 January 2022                  01:30              Clear   
4       Saturday 1 January 2022                  02:00              Clear   
5       Saturday 1 January 2022                  02:30              Clear   
6       Saturday 1 January 2022                  03:00              Clear   
7       Saturday 1 January 2022                  03:30              Clear   
8       Saturday 1 January 2022                  04:00              Clear   
9       Saturday 1 January 2022                  04:30              Clear   
10      Saturday 1 January 2022                  05:00              Clear   
11      Saturday 1 January 2022                  05:30        Fog Patches   
12      Saturday 1 January 2022                  06:00              Clear   
13      Saturday 1 January 2022                  06:30              Clear   
14      Saturday 1 January 2022                  07:00              Clear   
15      Saturday 1 January 2022                  07:30              Clear   
16      Saturday 1 January 2022                  08:00              Clear   
17      Saturday 1 January 2022                  08:30              Clear   
18      Saturday 1 January 2022                  09:00              Clear   
19      Saturday 1 January 2022                  09:30              Clear   
20      Saturday 1 January 2022                  10:00              Clear   
21      Saturday 1 January 2022                  10:30              Clear   
22      Saturday 1 January 2022                  11:00              Clear   
23      Saturday 1 January 2022                  11:30              Clear   
24      Saturday 1 January 2022                  12:00              Clear   
25      Saturday 1 January 2022                  12:30              Clear   
26      Saturday 1 January 2022                  13:00              Clear   
27      Saturday 1 January 2022                  13:30              Clear   
28      Saturday 1 January 2022                  14:00              Clear   
29      Saturday 1 January 2022                  14:30              Clear   
30      Saturday 1 January 2022                  15:00              Clear   
31      Saturday 1 January 2022                  15:30              Clear   
32      Saturday 1 January 2022                  16:00              Clear   
33      Saturday 1 January 2022                  16:30              Clear   
34      Saturday 1 January 2022                  17:00              Clear   
35      Saturday 1 January 2022                  17:30              Clear   
36      Saturday 1 January 2022                  18:00              Clear   
37      Saturday 1 January 2022                  18:30              Clear   
38      Saturday 1 January 2022                  19:00              Clear   
39      Saturday 1 January 2022                  19:30              Clear   
40      Saturday 1 January 2022                  20:00              Clear   
41      Saturday 1 January 2022                  20:30              Clear   
42      Saturday 1 January 2022                  21:00              Clear   
43      Saturday 1 January 2022                  21:30              Clear   
44      Saturday 1 January 2022                  22:00              Clear   
45      Saturday 1 January 2022                  22:30              Clear   
46      Saturday 1 January 2022                  23:00              Clear   
47      Saturday 1 January 2022                  23:30              Clear   
0         Monday 3 January 2022                  00:00              Clear   
1         Monday 3 January 2022                  00:30              Clear   
2         Monday 3 January 2022                  01:00              Clear   
3         Monday 3 Janua

In [32]:

pd.set_option('display.max_rows', None)
df = pd.concat(lst_df)
df[df.Condition == "Sunday"]
print(len(df))
df

1488


Day   Hour      Condition Temperature  Wind  \
0     Saturday 1 January 2022  00:00          Clear          5°     7   
1     Saturday 1 January 2022  00:30          Clear          5°     4   
2     Saturday 1 January 2022  01:00          Clear          3°     4   
3     Saturday 1 January 2022  01:30          Clear          3°     4   
4     Saturday 1 January 2022  02:00          Clear          3°     4   
5     Saturday 1 January 2022  02:30          Clear          3°     4   
6     Saturday 1 January 2022  03:00          Clear          3°     6   
7     Saturday 1 January 2022  03:30          Clear          2°     6   
8     Saturday 1 January 2022  04:00          Clear          1°     2   
9     Saturday 1 January 2022  04:30          Clear          2°     4   
10    Saturday 1 January 2022  05:00          Clear          1°     4   
11    Saturday 1 January 2022  05:30    Fog Patches          1°     4   
12    Saturday 1 January 2022  06:00          Clear          1°     6   
13    Saturday 1 January 2022  06:30          Clear          1°     4   
14    Saturday 1 January 2022  07:00          Clear          0°     4   
15    Saturday 1 January 2022  07:30          Clear          0°     4   
16    Saturday 1 January 2022  08:00          Clear          0°     6   
17    Saturday 1 January 2022  08:30          Clear          0°     6   
18    Saturday 1 January 2022  09:00          Clear          0°     4   
19    Saturday 1 January 2022  09:30          Clear          1°     2   
20    Saturday 1 January 2022  10:00          Clear          3°     2   
21    Saturday 1 January 2022  10:30          Clear          4°     6   
22    Saturday 1 January 2022  11:00          Clear          6°     6   
23    Saturday 1 January 2022  11:30          Clear          7°     4   
24    Saturday 1 January 2022  12:00          Clear          9°     2   
25    Saturday 1 January 2022  12:30          Clear         11°     2   
26    Saturday 1 January 2022  13:00          Clear         12°     2   
27    Saturday 1 January 2022  13:30          Clear         13°     2   
28    Saturday 1 January 2022  14:00          Clear         15°     2   
29    Saturday 1 January 2022  14:30          Clear         15°     4   
30    Saturday 1 January 2022  15:00          Clear         16°     2   
31    Saturday 1 January 2022  15:30          Clear         18°  Calm   
32    Saturday 1 January 2022  16:00          Clear         17°  Calm   
33    Saturday 1 January 2022  16:30          Clear         18°  Calm   
34    Saturday 1 January 2022  17:00          Clear         16°     2   
35    Saturday 1 January 2022  17:30          Clear         14°     4   
36    Saturday 1 January 2022  18:00          Clear         13°     6   
37    Saturday 1 January 2022  18:30          Clear         11°     2   
38    Saturday 1 January 2022  19:00          Clear         10°  Calm   
39    Saturday 1 January 2022  19:30          Clear          9°  Calm   
40    Saturday 1 January 2022  20:00          Clear          8°     6   
41    Saturday 1 January 2022  20:30          Clear          8°     6   
42    Saturday 1 January 2022  21:00          Clear          7°     4   
43    Saturday 1 January 2022  21:30          Clear          6°     7   
44    Saturday 1 January 2022  22:00          Clear          6°     7   
45    Saturday 1 January 2022  22:30          Clear          6°     7   
46    Saturday 1 January 2022  23:00          Clear          6°     6   
47    Saturday 1 January 2022  23:30          Clear          5°     6   
0       Sunday 2 January 2022  00:00          Clear          4°     4   
1       Sunday 2 January 2022  00:30          Clear          4°     4   
2       Sunday 2 January 2022  01:00          Clear          3°     2   
3       Sunday 2 January 2022  01:30          Clear          3°     6   
4       Sunday 2 January 2022  02:00          Clear          3°     6   
5       Sunday 2 January 2022  02:30          Clear          2°     4   
6       Sun